In [1]:
import pymupdf

In [33]:
doc = pymupdf.open(filename='../data/raw/aapl_2024.pdf')
doc2 = pymupdf.open(filename='../data/raw/tsla-2024.pdf')

In [55]:
for page in doc:
    print(page.get_text("dict"))

{'width': 612.0, 'height': 792.0, 'blocks': [{'number': 0, 'type': 0, 'bbox': (168.11000061035156, 58.49601745605469, 444.02197265625, 87.09599304199219), 'lines': [{'spans': [{'size': 13.0, 'flags': 20, 'bidi': 0, 'char_flags': 24, 'font': 'HelveticaLTStd-Bold', 'color': 0, 'alpha': 255, 'ascender': 0.7179999947547913, 'descender': -0.28200000524520874, 'text': 'UNITED STATES', 'origin': (254.3800048828125, 67.83001708984375), 'bbox': (254.3800048828125, 58.49601745605469, 357.6649169921875, 71.49601745605469)}], 'wmode': 0, 'dir': (1.0, 0.0), 'bbox': (254.3800048828125, 58.49601745605469, 357.6649169921875, 71.49601745605469)}, {'spans': [{'size': 13.0, 'flags': 20, 'bidi': 0, 'char_flags': 24, 'font': 'HelveticaLTStd-Bold', 'color': 0, 'alpha': 255, 'ascender': 0.7179999947547913, 'descender': -0.28200000524520874, 'text': 'SECURITIES AND EXCHANGE COMMISSION', 'origin': (168.11000061035156, 83.42999267578125), 'bbox': (168.11000061035156, 74.09599304199219, 444.02197265625, 87.09599

In [34]:
doc.get_toc()

[[1, 'Cover Page', 1],
 [1, 'TABLE OF CONTENTS', 3],
 [1, 'PART I', 4],
 [2, 'Item 1. Business', 4],
 [3, 'Company Background', 4],
 [3, 'Products', 4],
 [3, 'Services', 5],
 [3, 'Segments', 5],
 [3, 'Markets and Distribution', 5],
 [3, 'Competition', 5],
 [3, 'Supply of Components', 6],
 [3, 'Research and Development', 6],
 [3, 'Intellectual Property', 6],
 [3, 'Business Seasonality and Product Introductions', 7],
 [3, 'Human Capital', 7],
 [3, 'Available Information', 8],
 [2, 'Item 1A. Risk Factors', 8],
 [3, 'Macroeconomic and Industry Risks', 8],
 [3, 'Business Risks', 10],
 [3, 'Legal and Regulatory Compliance Risks', 16],
 [3, 'Financial Risks', 18],
 [3, 'General Risks', 20],
 [2, 'Item 1B. Unresolved Staff Comments', 20],
 [2, 'Item 1C. Cybersecurity', 20],
 [2, 'Item 2. Properties', 21],
 [2, 'Item 3. Legal Proceedings', 21],
 [2, 'Item 4. Mine Safety Disclosures', 21],
 [1, 'PART II', 22],
 [2,
  "Item 5. Market for Registrant's Common Equity, Related Stockholder Matters and

In [78]:
mpp = {}
for page in doc:
    for block in page.get_text("dict").get('blocks'):
        if block:
            # print(block)
            if 'lines' in block.keys():
                for line in block['lines']:
                    for span in line.get('spans'):
                        # print(span.get('size'))
                        size = span.get('size')
                        if size in mpp.keys():
                            mpp[size] += 1
                        else : mpp[size] = 1


In [79]:
baseLine = 9.0 
baseFreq = 0
for key,val in mpp.items():
    if val > baseFreq:
        baseLine = key
        val = baseFreq

In [80]:
baseLine

12.0

In [110]:
def find_headings(doc: pymupdf.Document, baseline_font_size: float) :
    headings = []
    font_size_threshold = 1.3

    for page_num, page in enumerate(doc, 1):
        blocks = page.get_text("dict").get("blocks", [])
        for block in blocks:
            if block.get("lines"):
                for line in block.get("lines"):
                    if line.get("spans"):
                        first_span = line["spans"][0]
                        span_size = first_span.get("size", 0)
                        

                        is_large_font = span_size > (baseline_font_size * font_size_threshold)
                        is_bold = first_span.get('flags') & pymupdf.TEXT_FONT_BOLD
                        is_italic = first_span.get('flags') & pymupdf.TEXT_FONT_ITALIC
                        if not is_italic and is_bold or is_large_font :
                            full_title = "".join(span.get("text", "") for span in line["spans"]).strip()
                            
                            if len(full_title) > 3:
                                headings.append({
                                    "title": full_title,
                                    "page": page_num,
                                    "bbox": line.get("bbox")  
                                })
    sorted_headings = sorted(headings, key=lambda h: (h["page"], h["bbox"][1]))
    
    return sorted_headings


In [113]:
sorted_headings = find_headings(doc,12.0)
for i in (sorted_headings):
    print(i)

{'title': 'UNITED STATES', 'page': 1, 'bbox': (254.3800048828125, 58.49601745605469, 357.6649169921875, 71.49601745605469)}
{'title': 'SECURITIES AND EXCHANGE COMMISSION', 'page': 1, 'bbox': (168.11000061035156, 74.09599304199219, 444.02197265625, 87.09599304199219)}
{'title': 'Washington, D.C. 20549', 'page': 1, 'bbox': (243.6999969482422, 89.69196319580078, 368.3960876464844, 100.69196319580078)}
{'title': 'FORM 10-K', 'page': 1, 'bbox': (260.2099914550781, 124.64397430419922, 351.7989807128906, 141.64398193359375)}
{'title': 'Apple Inc.', 'page': 1, 'bbox': (258.2099914550781, 306.75, 353.78997802734375, 326.75)}
{'title': 'California', 'page': 1, 'bbox': (143.88999938964844, 363.0579833984375, 185.39797973632812, 372.0579833984375)}
{'title': '94-2404110', 'page': 1, 'bbox': (423.3800048828125, 363.0579833984375, 471.4129943847656, 372.0579833984375)}
{'title': 'One Apple Park Way', 'page': 1, 'bbox': (120.6500015258789, 404.2980041503906, 208.67898559570312, 413.2980041503906)}
{'

In [116]:
def extract_text_between_headings(doc: pymupdf.Document, sorted_headings):
    """
    Extracts the text content for each section defined by a sorted list of headings.

    Args:
        doc: The PyMuPDF Document object.
        sorted_headings: A list of heading dictionaries, sorted by page and vertical position.

    Returns:
        A list of tuples, where each tuple is (section_name, section_text).
    """
    final_sections = []
    
    # Iterate through the headings to define the boundaries of each section
    for i in range(len(sorted_headings)):
        current_heading = sorted_headings[i]
        
        # The next heading in the list defines the end of the current section.
        # If it's the last heading, the section runs to the end of the document.
        if i + 1 < len(sorted_headings):
            next_heading = sorted_headings[i + 1]
        else:
            next_heading = None

        # --- Extraction Logic ---
        section_text = ""
        start_page = current_heading['page']
        # If it's the last section, it ends on the last page of the document.
        end_page = next_heading['page'] if next_heading else doc.page_count

        # --- Iterate through all pages that contain this section ---
        for page_num in range(start_page, end_page + 1):
            page = doc[page_num - 1]
            
            # Use page.get_text("blocks") which returns a list of tuples
            blocks = page.get_text("blocks")
            
            for block in blocks:
                # A block is a tuple: (x0, y0, x1, y1, text, block_type, block_no)
                block_y0 = block[1]  # The vertical position of the block's top
                
                # --- Conditionals to decide if a block belongs to the current section ---
                
                # Case 1: All blocks on pages between the start and end heading pages
                if page_num > start_page and page_num < end_page:
                    section_text += block[4] # block[4] is the text content
                
                # Case 2: Blocks on the same page as the start heading
                elif page_num == start_page:
                    # The block must be BELOW the current heading
                    if block_y0 > current_heading['bbox'][1]:
                        # And if the section ends on this same page, it must also be ABOVE the next heading
                        if end_page == start_page and next_heading and block_y0 < next_heading['bbox'][1]:
                            section_text += block[4]
                        # If the section spans multiple pages, take everything below the heading
                        elif end_page > start_page:
                            section_text += block[4]

                # Case 3: Blocks on the same page as the end heading
                elif page_num == end_page:
                    # The block must be ABOVE the next heading
                    if next_heading and block_y0 < next_heading['bbox'][1]:
                        section_text += block[4]

        # Add the classified name and the extracted text to our final list
        final_sections.append((current_heading.get('name', 'unknown'), section_text.strip()))

    return final_sections

In [117]:
fin = extract_text_between_headings(doc,sorted_headings)

In [115]:
sorted_headings

[{'title': 'UNITED STATES',
  'page': 1,
  'bbox': (254.3800048828125,
   58.49601745605469,
   357.6649169921875,
   71.49601745605469)},
 {'title': 'SECURITIES AND EXCHANGE COMMISSION',
  'page': 1,
  'bbox': (168.11000061035156,
   74.09599304199219,
   444.02197265625,
   87.09599304199219)},
 {'title': 'Washington, D.C. 20549',
  'page': 1,
  'bbox': (243.6999969482422,
   89.69196319580078,
   368.3960876464844,
   100.69196319580078)},
 {'title': 'FORM 10-K',
  'page': 1,
  'bbox': (260.2099914550781,
   124.64397430419922,
   351.7989807128906,
   141.64398193359375)},
 {'title': 'Apple Inc.',
  'page': 1,
  'bbox': (258.2099914550781, 306.75, 353.78997802734375, 326.75)},
 {'title': 'California',
  'page': 1,
  'bbox': (143.88999938964844,
   363.0579833984375,
   185.39797973632812,
   372.0579833984375)},
 {'title': '94-2404110',
  'page': 1,
  'bbox': (423.3800048828125,
   363.0579833984375,
   471.4129943847656,
   372.0579833984375)},
 {'title': 'One Apple Park Way',
  '

In [118]:
fin

[('unknown', ''),
 ('unknown', ''),
 ('unknown', ''),
 ('unknown',
  '(Mark One)\n☒    ANNUAL REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\nFor the fiscal year ended September\xa028, 2024\nor\n☐    TRANSITION REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934\nFor the transition period from \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0 to \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0.\nCommission File Number: 001-36743'),
 ('unknown', '(Exact name of Registrant as specified in its charter)'),
 ('unknown', ''),
 ('unknown',
  '(State or other jurisdiction\nof incorporation or organization)\n(I.R.S. Employer Identification No.)'),
 ('unknown', ''),
 ('unknown', ''),
 ('unknown', '(Address of principal executive offices)\n(Zip Code)'),
 ('unknown',
  'Securities registered pursuant to Section 12(b) of the Act:\nTitle of each class\nTrading \nsymbol(s)\nName of each exchange on which registered\nCommon Stock, $0.00001 par va

In [59]:
from sentence_transformers import SentenceTransformer
model_name = "all-MiniLM-L6-v2"
model = SentenceTransformer("all-MiniLM-L6-v2")

def embed_chunks(chunks):
    print(f"embedding : begin")
    embeddings = model.encode(chunks, show_progress_bar=True)
    print(f"embedding : end")
    return embeddings


In [54]:
import pymupdf
import logging

logger = logging.Logger(__name__)

def extract_text_from_pdf(file_path:str) -> str:
    print(f"loading file {file_path} : begin")
    # print(f"loading file {file_path} : begin")
    doc = pymupdf.open(filename=file_path)
    text = ""
    for page in doc:
        text += str(page.get_text().encode("utf-8"))

    # logger.log(1,msg=f"loading file {file_path} : end")
    print(f"loading file {file_path} : end")
    return text


In [55]:
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_text_splitters import SentenceTransformersTokenTextSplitter, SpacyTextSplitter

def chunk_text(text,chunk_size = 1000, chunk_overlap = 200):
    print(f"splitting text : begin")
    splitter = SentenceTransformersTokenTextSplitter(chunk_size = chunk_size,
                                              chunk_overlap = chunk_overlap,
                                              model_name="all-MiniLM-L6-v2")
    docs = splitter.split_text(text)
    print(f"text split into : {len(docs)} chunks")
    print(f"splitting text : end")
    return docs
    

In [46]:
doc = extract_text_from_pdf("../data/raw/aapl_2024.pdf")

loading file ../data/raw/aapl_2024.pdf : begin
loading file ../data/raw/aapl_2024.pdf : end


In [51]:
chunks = chunk_text(doc)

splitting text : begin
text split into : 2184 chunks
splitting text : end


In [56]:
embeds = embed_chunks(chunks)

embedding : begin


Batches: 100%|██████████| 69/69 [00:17<00:00,  3.98it/s]

embedding : end


In [63]:
len(embeds) == len(chunks)

True

In [80]:
CANONICAL_SECTIONS = {
    "business_overview": "Overview of the company's business, operations, core products/services, markets served, and strategic vision.",
    
    "management_discussion": "Management's discussion and analysis (MD&A) of financial condition, results of operations, liquidity, and capital resources.",
    
    "risk_factors": "Discussion of key risks, competitive threats, market uncertainties, and factors that could adversely affect performance.",
    
    "financial_highlights": "High-level summary of financial metrics such as revenue, EBITDA, margins, EPS, etc., typically discussed at the start of calls.",
    
    "financial_statements": "Tabular and textual presentation of balance sheet, income statement, cash flow statement, and supporting financial notes.",
    
    "legal_proceedings": "Details of current or potential lawsuits, regulatory investigations, or legal disputes involving the company.",
    
    "competitive_landscape": "Discussion of market competition, competitive advantages, and positioning relative to industry peers.",
    
    "macroeconomic_outlook": "Management commentary on broader economic trends (interest rates, inflation, geopolitics) impacting business operations.",
    
    "guidance_and_forecast": "Forward-looking statements, earnings guidance, and projections provided by management for upcoming quarters or years.",
    
    "strategic_initiatives": "New initiatives, restructuring plans, M&A activity, R&D investments, or geographic expansions underway or planned.",
    
    "capital_allocation": "Commentary on share buybacks, dividends, debt issuance/repayment, or capital expenditure strategies.",
    
    "esg_and_sustainability": "Environmental, social, and governance (ESG) initiatives, goals, disclosures, and impact reporting.",
    
    "executive_commentary": "Prepared remarks by CEO, CFO, or other executives typically given at the beginning of earnings calls.",
    
    "qna_session": "Unscripted analyst Q&A session, including responses from executives to investor/analyst questions.",
    
    "segment_reporting": "Breakdown of performance by business unit, geography, or product category with segment-specific commentary.",
    
    "revenue_drivers": "Detailed discussion of revenue growth drivers, including pricing, volume, customer trends, and product mix shifts.",
    
    "cost_and_margin_analysis": "Insights into COGS, SG&A, operating margins, and any material changes in expense structure.",
    
    "liquidity_and_cashflow": "Commentary on working capital, cash reserves, cash generation, and funding plans.",
    
    "shareholder_updates": "Messages directed at shareholders including investor relations, annual meeting notes, or equity structure changes.",
    
    "accounting_changes": "Disclosure of changes in accounting policy, restatements, or unusual adjustments affecting financials.",
    
    "regulatory_updates": "New government policies, compliance mandates, or industry-specific regulation affecting operations.",
    
    "human_capital": "Talent strategy, layoffs/hiring, DEI updates, employee productivity, or labor-related discussions.",
    
    "technology_and_innovation": "Commentary on new tech initiatives, digital transformation, software systems, or intellectual property."
}


In [81]:
section_names = list(CANONICAL_SECTIONS.keys())
section_descriptions = list(CANONICAL_SECTIONS.values())
section_embeddings = model.encode(section_descriptions,show_progress_bar=True)
client = chromadb.Client()
section_collection = client.get_or_create_collection("section_embeddings")

section_collection.add(
    documents=section_descriptions,
    embeddings=[e.tolist() for e in section_embeddings],
    ids=section_names,
    metadatas=[{"section": name} for name in section_names]
)




Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches: 100%|██████████| 1/1 [00:00<00:00,  1.64it/s]


In [ ]:
def assign_sections_to_chunks(chunks, chunk_embeddings, top_k=2, similarity_threshold=0.65):
    labeled_chunks = []

    for chunk, chunk_embed in zip(chunks, chunk_embeddings):
        results = section_collection.query(
            query_embeddings=[chunk_embed.tolist()],
            n_results=top_k
        )

        sections = results["ids"][0]
        scores = results["distances"][0]

        final_labels = []
        for section, distance in zip(sections, scores):
            if distance < (2 - similarity_threshold): 
                final_labels.append(section)

        if not final_labels:
            final_labels = ["general_body"]

        labeled_chunks.append({
            "chunk": chunk,
            
            "assigned_sections": final_labels,
            "raw_distances": scores[:len(final_labels)],
        })

    return labeled_chunks

In [83]:
labeled = assign_sections_to_chunks(chunks,embeds)

In [84]:
labeled

[{'chunk': "b ' united states \\ nsecurities and exchange commission \\ nwashington, d. c. 20549 \\ nform 10 - k \\ n ( mark one ) \\ n \\ xe2 \\ x98 \\ x92 annual report pursuant to section 13 or 15 ( d ) of the securities exchange act of 1934 \\ nfor the fiscal year ended september \\ xc2 \\ xa028, 2024 \\ nor \\ n \\ xe2 \\ x98 \\ x90 transition report pursuant to section 13 or 15 ( d ) of the securities exchange act of 1934 \\ nfor the transition period from \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 to \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\ xc2 \\ xa0 \\",
  'assigned_sections': ['general_body'],
  'raw_distances': [1.4544795751571655]},
 {'chunk': '( d ) of the securities exchange act of 1934 \\ nfor the fiscal year ended september \\ xc2 \\ xa028, 2024 \\ nor \\ n \\ xe2 \\ x98 \\ x90 transition report pursuant to section 13 or 15 ( d ) of the securi